Importing all required libraries

In [21]:
import sys
import numpy as np 
import pandas as pd
import matplotlib as mpl
import matplotlib.pyplot as plt
import folium

loading in dataset

In [22]:
df = pd.read_csv('COVID19 cases.csv',index_col = 0)
df_pop = pd.read_csv('NeighbourhoodPopulation.csv',index_col = 0)
df_pop

population  population density
Neighbourhood                                               
Agincourt North                    29113                3929
Agincourt South-Malvern West       23757                3034
Alderwood                          12054                2435
Annex                              30526               10863
Banbury-Don Mills                  27695                2775
...                                  ...                 ...
Wychwood                           14349                8541
Yonge-Eglinton                     11817                7162
Yonge-St.Clair                     12528               10708
York University Heights            27593                2086
Yorkdale-Glen Park                 14804                2451

[140 rows x 2 columns]

In [23]:
 local = df["Neighbourhood Name"] == "Humewood-Cedarvale"
 active = df["Outcome"] == "ACTIVE"
 travel = df["Source of Infection"] == "Travel"
 outbreak = df["Outbreak Associated"] == "Outbreak Associated"


In [24]:
df['count'] = 1
# creating new dataframe with all covid cases by neighbourhood
df_NeighbourhoodNew = df.groupby('Neighbourhood Name',axis = 0).count() 
df_NeighbourhoodNew.drop(['Assigned_ID', 'Outbreak Associated','Age Group', 'FSA', 'Source of Infection', 'Classification', 'Episode Date', 'Reported Date','Client Gender', 'Outcome','Currently Hospitalized', 'Currently in ICU', 'Currently Intubated','Ever Hospitalized','Ever in ICU','Ever Intubated'],axis = 1, inplace = True)
df_NeighbourhoodNew = df_NeighbourhoodNew.sort_values(by = 'Neighbourhood Name', ascending = True)
df_NeighbourhoodNew = pd.concat([df_NeighbourhoodNew, df_pop], axis=1)
df_NeighbourhoodNew.reset_index(level=0, inplace=True)
df_NeighbourhoodNew['Cases per 1000 People'] = df_NeighbourhoodNew['count'].div(df_NeighbourhoodNew['population']).mul(1000)
df_NeighbourhoodNew['Cases per Sqaure KM'] = df_NeighbourhoodNew['count'].div(df_NeighbourhoodNew['population'].div(df_NeighbourhoodNew['population density']))
df_NeighbourhoodNew.rename(columns = {'index': 'Neighbourhood Name'}, inplace = True)
df_NeighbourhoodNew



Neighbourhood Name  count  population  population density  \
0                 Agincourt North    714       29113                3929   
1    Agincourt South-Malvern West    579       23757                3034   
2                       Alderwood    249       12054                2435   
3                           Annex    592       30526               10863   
4               Banbury-Don Mills    420       27695                2775   
..                            ...    ...         ...                 ...   
135                      Wychwood    273       14349                8541   
136                Yonge-Eglinton    124       11817                7162   
137                Yonge-St.Clair    135       12528               10708   
138       York University Heights   1606       27593                2086   
139            Yorkdale-Glen Park    829       14804                2451   

     Cases per 1000 People  Cases per Sqaure KM  
0                24.525126            96.359221  
1                24.371764            73.943932  
2                20.657043            50.299900  
3                19.393304           210.669462  
4                15.165192            42.083409  
..                     ...                  ...  
135              19.025716           162.498641  
136              10.493357            75.153423  
137              10.775862           115.387931  
138              58.203167           121.411807  
139              55.998379           137.252026  

[140 rows x 6 columns]

In [25]:
neighbourhood_map = folium.Map(location=[43.6532, -79.3832], zoom_start=11)
casesperkm_map = folium.Map(location=[43.6532, -79.3832], zoom_start=11)
casesper1000p_map = folium.Map(location=[43.6532, -79.3832], zoom_start=11)

In [26]:
toronto_geo = os.path.join('toronto_neighbourhood.geojson')

v1 = np.linspace(df_NeighbourhoodNew['count'].min(),
                              df_NeighbourhoodNew['count'].max(),
                              10, dtype=int)
v1 = v1.tolist() # change the numpy array to a list
v1[-1] = v1[-1] + 1 # make sure that the last value of the list is greater than the maximum immigration

v2 = np.linspace(df_NeighbourhoodNew['Cases per Sqaure KM'].min(),
                              df_NeighbourhoodNew['Cases per Sqaure KM'].max(),
                              10, dtype=int)
v2 = v2.tolist() # change the numpy array to a list
v2[-1] = v2[-1] + 1 # make sure that the last value of the list is greater than the maximum immigration

v3 = np.linspace(df_NeighbourhoodNew['Cases per 1000 People'].min(),
                              df_NeighbourhoodNew['Cases per 1000 People'].max(),
                              10, dtype=int)
v3 = v3.tolist() # change the numpy array to a list
v3[-1] = v3[-1] + 1 # make sure that the last value of the list is greater than the maximum immigration


In [27]:
neighbourhood_map.choropleth(
    geo_data = toronto_geo,
    name = 'toronto covid map',
    data = df_NeighbourhoodNew,
    columns=['Neighbourhood Name', 'count'],
    key_on='feature.properties.AREA_NAME',
    threshold_scale = v1,
    fill_color = 'YlOrRd',
    fill_opacity = 0.7,
    line_opacity = 0.2,
    legend_name = 'Toronto Covid Map'
)
casesperkm_map.choropleth(
    geo_data = toronto_geo,
    name = 'toronto covid map',
    data = df_NeighbourhoodNew,
    columns=['Neighbourhood Name', 'Cases per Sqaure KM'],
    key_on='feature.properties.AREA_NAME',
    threshold_scale = v2,
    fill_color = 'YlOrRd',
    fill_opacity = 0.7,
    line_opacity = 0.2,
    legend_name = 'Toronto Active Covid Map'
)
casesper1000p_map.choropleth(
    geo_data = toronto_geo,
    data = df_NeighbourhoodNew,
    columns=['Neighbourhood Name', 'Cases per 1000 People'],
    key_on='feature.properties.AREA_NAME',
    threshold_scale = v3,
    fill_color = 'YlOrRd',
    fill_opacity = 0.7,
    line_opacity = 0.2,
    legend_name = 'Toronto Covid Cases per 1000 people'
)

In [28]:
neighbourhood_map

In [29]:
casesper1000p_map

In [30]:
casesperkm_map